In [ ]:
# Name: Wenqi Wang
# Github username: acse-ww721

# 1 ASOS_DATA PROCESSING

## Process raw_data time

In [ ]:
"""VERSION 2"""


In [1]:
# Basic setting for Jupyter_notebook to import utils
import os
import sys

notebook_path = os.path.abspath("")
project_root = os.path.abspath(os.path.join(notebook_path, "../../"))

sys.path.append(project_root)

In [34]:
import os
import pandas as pd
from tqdm import tqdm
from datetime import datetime, timedelta
from utils import folder_utils

In [4]:
# Example usage

country = "GB"
data_folder = "data"
data_read_category = "raw_data"
data_save_category = "processed_data"
output_folder = "ASOS_DATA"

In [10]:
def get_csv_list(country, data_folder, data_category, output_folder):
    # Specify the folder path
    input_folder_path = folder_utils.find_folder(
        country, data_folder, data_category, output_folder
    )
    # Initialize a dataframe to store all the data from the same country
    raw_df = pd.DataFrame()
    # Get the filenames of all CSV files under the folder except the station network file
    csv_files = [
        f
        for f in os.listdir(input_folder_path)
        if f.endswith(".csv") and "asos_station_network" not in f
    ]
    # Add path
    csv_file_paths = []  # Initialize a list to store the path of all csv files
    station_list = []  # Initialize a list to store the station name of all csv files
    for csv_file in tqdm(csv_files):
        csv_path = os.path.join(input_folder_path, csv_file)
        # Extract station from the filename
        station = csv_file.split("_")[1]
        csv_file_paths.append(csv_path)
        station_list.append(station)

    return csv_file_paths, station_list

In [47]:
def extract_data_to_df(country, data_folder, data_category, output_folder):
    # Specify the folder path
    input_folder_path = folder_utils.find_folder(
        country, data_folder, data_category, output_folder
    )
    # Initialize a dataframe to store all the data from the same country
    raw_df = pd.DataFrame()
    # Get the filenames of all CSV files under the folder except the station network file
    csv_files = [
        f
        for f in os.listdir(input_folder_path)
        if f.endswith('.csv') and "asos_station_network" not in f
    ]
    # Read and merge the csv files in queue
    for csv_file in tqdm(csv_files):
        csv_file_path = os.path.join(input_folder_path, csv_file)
        df = pd.read_csv(csv_file_path)
        raw_df = pd.concat([raw_df, df], ignore_index=True)

    return raw_df

In [76]:
def time_rearrange(df):
    """
    For hourly initial times (such as 01:00:00, 02:00:00, etc.), hold.
    For the 20th minute of every hour (such as 01:20:00, 02:20:00, etc.),
    check whether the previous full point exists, and delete the 20-minute data if it exists,
    otherwise change to the previous full point.
    For the 50th minute of every hour (such as 01:50:00, 02:50:00, etc.),
    check whether the next full point exists, and if it exists, delete the 50-minute data,
    otherwise change to the next full point

    df is a DataFrame with a column named 'valid' containing time strings.
    Return the processed DataFrame.
    """
    # Create an assistant volume and convert time strings to datetime objects
    df["valid_datetime"] = pd.to_datetime(df["valid"], format="%Y-%m-%d %H:%M")

    # Delete the data before 1979-01-01
    cutoff_date = datetime(1979, 1, 1)

    # Check if the earliest date is after the cutoff date
    earliest_date = df["valid_datetime"].min()
    if earliest_date >= cutoff_date:
        print(
            f"The start date :  ({earliest_date.strftime('%d/%m/%Y')}) is after 19790101, terminate cutoff."
        )

    df = df[df["valid_datetime"] >= cutoff_date]

    # Create a list to store the indexes of rows to be deleted
    to_delete = []

    for index, row in tqdm(df.iterrows()):
        current_time = row["valid_datetime"]

        # If the minute is 20 minutes
        if current_time.minute == 20:
            prev_hour_time = current_time.replace(minute=0, second=0)
            if (
                prev_hour_time in df["valid_datetime"].values
            ):  # if the previous full point exists
                to_delete.append(index)  # record the current index for later deletion
            else:
                df.at[
                    index, "valid_datetime"
                ] = prev_hour_time  # otherwise change to the previous full point

        # if the minute is 50 minutes
        elif current_time.minute == 50:
            next_hour_time = (current_time + timedelta(hours=1)).replace(
                minute=0, second=0
            )
            if (
                next_hour_time in df["valid_datetime"].values
            ):  # if the next full point exists
                to_delete.append(index)  # record the current index for later deletion
            else:
                df.at[
                    index, "valid_datetime"
                ] = next_hour_time  # otherwise change to the next full point

    # delete the rows that need to be deleted
    df.drop(to_delete, inplace=True)

    # Delete the original time column
    df.drop(columns=["valid"], inplace=True)

    # Rename the new time column and  it save as iso 8601 format as datetime64[ns] automatically
    df.rename(columns={"valid_datetime": "time"}, inplace=True)
    # df["time"] = df["time"].dt.strftime("%Y-%m-%dT%H:%M:%S.%f")

    return df

In [77]:
def process_asos_rawdata(raw_df):
    """
    Unified variable unit based on era5
    station: three or four character site identifier
    valid: observation time in UTC
    tmpc: Air Temperature in Celsius, typically @ 2 meters

    """

    # time preprocessing
    processed_df = time_rearrange(raw_df)


    # Convert Celsius to Kelvin for "tmpc" and rename the column
    processed_df.rename(columns={"tmpc": "t2m"}, inplace=True)
    processed_df["t2m"] = processed_df["t2m"] + 273.15
    processed_df["t2m"] = processed_df["t2m"].round(1)

    return processed_df

In [67]:
def save_asos_processed_data(
    processed_df, station, country, data_folder, data_category, output_folder
):
    output_directory = folder_utils.create_folder(
        country, data_folder, data_category, output_folder
    )
    output_filename = f"{country}_ASOS_{station}_processed_data.csv"
    output_filepath = os.path.join(output_directory, output_filename)
    processed_df.to_csv(output_filepath, index=False, encoding="utf-8")
    print(f"{output_filepath} done!")


## Test example

### Test example 1

In [12]:
# Example usage

country = "GB"
data_folder = "data"
data_read_category = "raw_data"
data_test_category = "test_data"
data_save_category = "processed_data"
output_folder = "ASOS_DATA"

In [60]:
csv_path, station_list = get_csv_list(
    country, data_folder, data_test_category, output_folder
)

100%|██████████████████████████████████████████| 2/2 [00:00<00:00, 21732.15it/s]


In [61]:
station_list

['EGSH', 'EGHC']

In [62]:
csv_path

['/Users/ww721/JupyterNotebookPath/IRP_20220602/irp_ww721_bakcup/data/test_data/ASOS_DATA/GB_ASOS_DATA/GB_EGSH_19760101_20230101.csv',
 '/Users/ww721/JupyterNotebookPath/IRP_20220602/irp_ww721_bakcup/data/test_data/ASOS_DATA/GB_ASOS_DATA/GB_EGHC_19760101_20230101.csv']

In [47]:
raw_df = pd.read_csv(csv_path[1])

In [48]:
raw_df

station             valid  tmpc
0         EGHC  1976-01-01 00:00   9.0
1         EGHC  1976-01-01 03:00   9.0
2         EGHC  1976-01-01 06:00   9.0
3         EGHC  1976-01-01 09:00   8.0
4         EGHC  1976-01-01 12:00  10.0
...        ...               ...   ...
102565    EGHC  2022-12-31 08:20  12.0
102566    EGHC  2022-12-31 08:50  12.0
102567    EGHC  2022-12-31 09:20  12.0
102568    EGHC  2022-12-31 09:50  11.0
102569    EGHC  2022-12-31 10:20  11.0

[102570 rows x 3 columns]

In [49]:
processed_df = process_asos_rawdata(raw_df)

93955it [00:05, 16008.67it/s]
/var/folders/tt/fs_l1by51m30s907pzxq6gf40000gp/T/ipykernel_17872/356943810.py:62: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.drop(to_delete, inplace=True)
/var/folders/tt/fs_l1by51m30s907pzxq6gf40000gp/T/ipykernel_17872/356943810.py:65: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.drop(columns=["valid"], inplace=True)
/var/folders/tt/fs_l1by51m30s907pzxq6gf40000gp/T/ipykernel_17872/356943810.py:68: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guid

In [50]:
processed_df

station    t2m                time
8615      EGHC  270.2 1979-01-01 00:00:00
8616      EGHC  269.2 1979-01-01 03:00:00
8617      EGHC  270.2 1979-01-01 06:00:00
8618      EGHC  270.2 1979-01-01 09:00:00
8619      EGHC  271.2 1979-01-01 12:00:00
...        ...    ...                 ...
102562    EGHC  283.2 2022-12-30 17:00:00
102563    EGHC  285.2 2022-12-31 07:00:00
102564    EGHC  285.2 2022-12-31 08:00:00
102566    EGHC  285.2 2022-12-31 09:00:00
102568    EGHC  284.2 2022-12-31 10:00:00

[76862 rows x 3 columns]

---

---


### Test example 2

In [78]:
csv_list, station_list = get_csv_list(
    country, data_folder, data_test_category, output_folder
)

100%|██████████████████████████████████████████| 2/2 [00:00<00:00, 23045.63it/s]


In [71]:
raw_df_2 

station             valid   tmpc
0         EGSH  1987-12-02 00:00   5.40
1         EGSH  1987-12-02 01:00   4.80
2         EGSH  1987-12-02 02:00   4.70
3         EGSH  1987-12-02 03:00    NaN
4         EGSH  1987-12-02 04:00   4.44
...        ...               ...    ...
474463    EGSH  2022-12-31 21:50  13.00
474464    EGSH  2022-12-31 22:20  12.00
474465    EGSH  2022-12-31 22:50  12.00
474466    EGSH  2022-12-31 23:20  12.00
474467    EGSH  2022-12-31 23:50  12.00

[474468 rows x 3 columns]

In [80]:
processed_df_2 = process_asos_rawdata(raw_df_2)

The start date :  (02/12/1987) is after 19790101, terminate cutoff.


16227it [00:02, 5425.17it/s]


KeyboardInterrupt: 

## Processing all station data

In [81]:
csv_list, station_list = get_csv_list(
    country, data_folder, data_read_category, output_folder
)

100%|█████████████████████████████████████| 112/112 [00:00<00:00, 336264.89it/s]


In [ ]:
for csv_path, station in tqdm(zip(csv_list, station_list)):
    print(csv_path)
    try:
        raw_df = pd.read_csv(csv_path)
        processed_df = process_asos_rawdata(raw_df)
        save_asos_processed_data(
            processed_df,
            station,
            country,
            data_folder,
            data_save_category,
            output_folder,
        )
    except Exception as e:
        print(f"An error occurred for {csv_path}: {e}")
        continue  # Continue to the next iteration


0it [00:00, ?it/s]

/Users/ww721/JupyterNotebookPath/IRP_20220602/irp_ww721_bakcup/data/raw_data/ASOS_DATA/GB_ASOS_DATA/GB_EGYH_19760101_20230101.csv



0it [00:00, ?it/s]
761it [00:00, 7609.01it/s]
7649it [00:00, 43646.72it/s]
14119it [00:00, 53255.64it/s]
21055it [00:00, 59609.67it/s]
28011it [00:00, 63195.27it/s]
34960it [00:00, 65333.05it/s]
41938it [00:00, 66783.91it/s]
48925it [00:00, 67764.16it/s]
55907it [00:00, 68404.47it/s]
62862it [00:01, 68755.08it/s]
69738it [00:01, 65909.21it/s]
76481it [00:01, 66355.35it/s]
83135it [00:01, 65472.90it/s]
89885it [00:01, 66068.71it/s]
96504it [00:01, 63693.29it/s]
102897it [00:01, 62288.76it/s]
109145it [00:01, 59543.85it/s]
115129it [00:01, 44720.31it/s]
120139it [00:02, 34701.18it/s]
124272it [00:02, 30357.49it/s]
127806it [00:02, 27546.73it/s]
130901it [00:02, 25970.27it/s]
133712it [00:02, 24050.82it/s]
136250it [00:02, 23269.74it/s]
138653it [00:03, 22912.63it/s]
140989it [00:03, 22384.18it/s]
143250it [00:03, 21775.38it/s]
145558it [00:03, 22097.73it/s]
147780it [00:03, 21674.83it/s]
150060it [00:03, 21973.36it/s]
152265it [00:03, 21700.29it/s]
154549it [00:03, 22019.49it/s]
156756i

Folder '/Users/ww721/JupyterNotebookPath/IRP_20220602/irp_ww721_bakcup/data/processed_data/ASOS_DATA/GB_ASOS_DATA' created successfully.


1it [00:15, 15.30s/it]

...

109it [7:00:24, 169.99s/it]

/Users/ww721/JupyterNotebookPath/IRP_20220602/irp_ww721_bakcup/data/processed_data/ASOS_DATA/GB_ASOS_DATA/GB_ASOS_EGPM_processed_data.csv done!
/Users/ww721/JupyterNotebookPath/IRP_20220602/irp_ww721_bakcup/data/raw_data/ASOS_DATA/GB_ASOS_DATA/GB_EGMD_19760101_20230101.csv
The start date :  (05/01/1988) is after 19790101, terminate cutoff.



0it [00:00, ?it/s]
1it [00:00,  8.76it/s]
250it [00:00, 1387.60it/s]
497it [00:00, 1865.32it/s]
744it [00:00, 2097.15it/s]
990it [00:00, 2224.88it/s]
1236it [00:00, 2303.97it/s]
1482it [00:00, 2353.55it/s]
1731it [00:00, 2394.79it/s]
1977it [00:00, 2414.28it/s]
2222it [00:01, 2422.93it/s]
2470it [00:01, 2438.34it/s]
2717it [00:01, 2446.98it/s]
2965it [00:01, 2454.07it/s]
3214it [00:01, 2463.82it/s]
3462it [00:01, 2466.35it/s]
3709it [00:01, 2466.65it/s]
3956it [00:01, 2464.11it/s]
4204it [00:01, 2467.92it/s]
4451it [00:01, 2464.42it/s]
4698it [00:02, 2466.00it/s]
4945it [00:02, 2429.45it/s]
5189it [00:02, 2413.84it/s]
5433it [00:02, 2418.87it/s]
5676it [00:02, 2420.18it/s]
5919it [00:02, 2419.71it/s]
6162it [00:02, 2421.05it/s]
6405it [00:02, 2411.69it/s]
6647it [00:02, 2342.36it/s]
6882it [00:02, 2132.88it/s]
7099it [00:03, 2134.15it/s]
7315it [00:03, 2135.97it/s]
7531it [00:03, 2102.16it/s]
7751it [00:03, 2129.98it/s]
7997it [00:03, 2225.39it/s]
8238it [00:03, 2279.02it/s]
8479it [0

Folder '/Users/ww721/JupyterNotebookPath/IRP_20220602/irp_ww721_bakcup/data/processed_data/ASOS_DATA/GB_ASOS_DATA' created successfully.
/Users/ww721/JupyterNotebookPath/IRP_20220602/irp_ww721_bakcup/data/processed_data/ASOS_DATA/GB_ASOS_DATA/GB_ASOS_EGHQ_processed_data.csv done!
/Users/ww721/JupyterNotebookPath/IRP_20220602/irp_ww721_bakcup/data/raw_data/ASOS_DATA/GB_ASOS_DATA/GB_EGGD_19760101_20230101.csv
The start date :  (05/01/1988) is after 19790101, terminate cutoff.



0it [00:00, ?it/s]
1it [00:00,  2.10it/s]
118it [00:00, 270.97it/s]
236it [00:00, 495.09it/s]
354it [00:00, 673.40it/s]
475it [00:00, 817.40it/s]
595it [00:00, 922.41it/s]
715it [00:01, 999.87it/s]
833it [00:01, 1050.82it/s]
952it [00:01, 1091.29it/s]
1071it [00:01, 1119.43it/s]
1190it [00:01, 1138.79it/s]
1309it [00:01, 1153.28it/s]
1430it [00:01, 1168.44it/s]
1549it [00:01, 1173.76it/s]
1669it [00:01, 1180.70it/s]
1788it [00:01, 1181.65it/s]
1907it [00:02, 1182.20it/s]
2026it [00:02, 1181.02it/s]
2147it [00:02, 1186.76it/s]
2266it [00:02, 1184.05it/s]
2385it [00:02, 1185.08it/s]
2504it [00:02, 1186.05it/s]
2623it [00:02, 1184.66it/s]
2744it [00:02, 1190.02it/s]
2866it [00:02, 1197.07it/s]
2987it [00:02, 1198.52it/s]
3109it [00:03, 1204.07it/s]
3230it [00:03, 1196.25it/s]
3350it [00:03, 1172.82it/s]
3468it [00:03, 1113.02it/s]
3580it [00:03, 1096.95it/s]
3691it [00:03, 1091.72it/s]
3803it [00:03, 1099.85it/s]
3918it [00:03, 1112.22it/s]
4033it [00:03, 1122.56it/s]
4151it [00:04, 1137

## Merge station info and convert csv to nc by year

### The regird attempt

In [100]:
# Basic setting for Jupyter_notebook to import utils
import os
import sys

notebook_path = os.path.abspath("")
project_root = os.path.abspath(os.path.join(notebook_path, "../../"))

sys.path.append(project_root)

In [110]:
import os
import gc
import pandas as pd
from tqdm import tqdm
from datetime import datetime, timedelta
from utils import folder_utils
import re
import xarray as xr
import numpy as np
import xesmf as xe
import dask.dataframe as dd

In [111]:
def regrid(ds_in, ddeg_out_lat, ddeg_out_lon, method="bilinear", reuse_weights=False):
    """
    Regrid horizontally (longitude direction).
    :param ds_in: Input xarray dataset
    :param ddeg_out_lat: Output resolution latitude
    :param ddeg_out_lon: Output resolution longitude
    :param method: Regridding method
    :param reuse_weights: Reuse weights for regridding
    :return: ds_out: Regridded dataset
    """
    # Rename to ESMF compatible coordinates
    if "latitude" in ds_in.coords:
        ds_in = ds_in.rename({"latitude": "lat", "longitude": "lon"})

    # Create output grid
    grid_out = xr.Dataset(
        {
            "lat": (["lat"], np.arange(50, 58, ddeg_out_lat)),  # 50 - 57.75
            "lon": (["lon"], np.arange(-6, 2.0, ddeg_out_lon)),  # -6 - 1.875
        }
    )

    # Create regridder
    regridder = xe.Regridder(
        ds_in,
        grid_out,
        method,
        periodic=False,  # For a specific region, set periodic to False
        reuse_weights=False,  # recalculat weight automatically
    )

    # Hack to speed up regridding of large files
    ds_list = []
    chunk_size = 500
    n_chunks = len(ds_in.time) // chunk_size + 1
    for i in range(n_chunks):
        ds_small = ds_in.isel(time=slice(i * chunk_size, (i + 1) * chunk_size))
        ds_list.append(regridder(ds_small).astype("float32"))
    ds_out = xr.concat(ds_list, dim="time")

    # Set attributes since they get lost during regridding
    for var in ds_out:
        ds_out[var].attrs = ds_in[var].attrs
    ds_out.attrs.update(ds_in.attrs)

    # Regrid dataset
    # ds_out = regridder(ds_in)
    return ds_out

### Test to merge all asos data by station and then divide all the data by year 

In [119]:
def merge_csv_station(country, data_folder, data_category, output_folder):
    """Merge all csv files in the folder and add station latlon information"""

    # Process station_network
    try:
        input_folder = folder_utils.find_folder(
            country, data_folder, data_category, output_folder
        )

        station_network_csv = "GB__asos_station_network.csv"
        station_network_csv_path = os.path.join(input_folder, station_network_csv)

        # Read station network CSV
        station_id_df = pd.read_csv(station_network_csv_path)

        columns_to_keep = [
            "ID",
            "Latitude",
            "Logitude",
        ]

        station_id_df = station_id_df[columns_to_keep]
        rename_mapping = {
            "ID": "station",
            "Latitude": "latitude",
            "Logitude": "longitude",  # Fixed the typo
        }

        station_id_df.rename(columns=rename_mapping, inplace=True)

        # Check if input folder is empty
        files_in_directory = os.listdir(input_folder)
        if not files_in_directory:
            print("Error: The specified folder is empty.")
            return None

        # Iterate through CSV files in the folder
        merged_df_list = []
        for filename in tqdm(files_in_directory):
            if filename.startswith("GB_ASOS_") and filename.endswith("_processed_data.csv"):
                csv_path = os.path.join(input_folder, filename)

                # Use chunk reading for large files
                chunk_size = 10000  # Adjust as needed
                chunks = pd.read_csv(csv_path, chunksize=chunk_size)
                for chunk in chunks:
                    try:
                        merged_df = pd.merge(station_id_df, chunk, on="station", how="left")
                        merged_df_list.append(merged_df)
                    except Exception as e:
                        print(f"Error processing chunk in file {filename}: {e}")
                del chunk

        # Concatenate all dataframes in the list
        merged_df_all = pd.concat(merged_df_list, ignore_index=True)
        desired_order = ["latitude", "longitude", "time", "t2m"]
        merged_df_all = merged_df_all[desired_order]
        # Drop duplicates based on time, latitude, and longitude
        merged_df_all = merged_df_all.drop_duplicates(subset=['time', 'latitude', 'longitude'])

        # After merging all the dataframes and dropping duplicates:
        # Convert 'time' column to datetime type
        merged_df_all['time'] = pd.to_datetime(merged_df_all['time']) # re-ensure the dtype

        # Group by year
        grouped = merged_df_all.groupby(merged_df_all['time'].dt.year)

        # Save each group as a CSV
        output_directory = folder_utils.find_folder(
            country, data_folder, data_category, output_folder
        )
        year_list = []
        for year, group in tqdm(grouped):
            # year =year.astype(int)
            output_filename = f"{country}_merged_ASOS_{year}.csv"
            output_path = os.path.join(output_directory, output_filename)
            group.to_csv(output_path, index=False, encoding="utf-8")
            year_list.append(year)
            print(f"{output_path} saved!")

        del merged_df_list  # Further release memory

        return year_list
    except Exception as e:
        print(f"Error processing files: {e}")
        return None

In [113]:
def get_asos_year_list(country, data_folder, data_category, output_folder):
    input_folder_path = folder_utils.find_folder(
        country, data_folder, data_category, output_folder
    )
    csv_files = [
        f for f in os.listdir(input_folder_path) if f.endswith(".csv") and "_merged_ASOS_" in f
    ]
    return [
        os.path.join(input_folder_path, csv_file) for csv_file in csv_files
    ]  # list for asos year files path

In [114]:
def csv_to_nc4(merged_csv_path,year, country, data_folder, data_category, output_folder):
    """Convert the merged CSV file to netCDF4 format by year."""
    df = pd.read_csv(merged_csv_path)
    ds_in = xr.Dataset.from_dataframe(df.set_index(['latitude', 'longitude', 'time']))
    ds_in = ds_in.sel(latitude=slice(50, 58), longitude=slice(-6, 2))
    ddeg_out_lat = 0.25
    ddeg_out_lon = 0.125
    regridded_ds = regrid(ds_in, ddeg_out_lat, ddeg_out_lon, method="bilinear", reuse_weights=False)

    output_directory = folder_utils.find_folder(country,data_folder,data_category,output_folder)
    output_filename = f"{country}_ASOS_regird_{year}.nc"
    output_path = os.path.join(output_directory, output_filename)
    regridded_ds.to_netcdf(output_path)
    print(f"{output_filename} done!")

In [115]:
# Example usage

country = "GB"
data_folder = "data"
data_read_category = "raw_data"
data_test_category = "test_data"
data_save_category = "processed_data"
output_folder = "ASOS_DATA"


In [121]:
def get_year(start_year, end_year):
    # start_year = 1979
    # end_year = 2023
    year_list = list(range(start_year, end_year + 1))

    # Convert the integer list to a string list
    year_str_list = [str(year) for year in year_list]
    
    return year_str_list

In [122]:
start_year = 1979
end_year = 2023
year_str_list = get_year(start_year, end_year)
year_str_list

['1979',
 '1980',
 '1981',
 '1982',
 '1983',
 '1984',
 '1985',
 '1986',
 '1987',
 '1988',
 '1989',
 '1990',
 '1991',
 '1992',
 '1993',
 '1994',
 '1995',
 '1996',
 '1997',
 '1998',
 '1999',
 '2000',
 '2001',
 '2002',
 '2003',
 '2004',
 '2005',
 '2006',
 '2007',
 '2008',
 '2009',
 '2010',
 '2011',
 '2012',
 '2013',
 '2014',
 '2015',
 '2016',
 '2017',
 '2018',
 '2019',
 '2020',
 '2021',
 '2022',
 '2023']

In [125]:
csv_paths = get_asos_year_list(country,data_folder,data_save_category,output_folder)
csv_paths

['F:\\JuPyterNotebook\\irp_ww721_bakcup\\data\\processed_data\\ASOS_DATA\\GB_ASOS_DATA\\GB_merged_ASOS_1979.csv',
 'F:\\JuPyterNotebook\\irp_ww721_bakcup\\data\\processed_data\\ASOS_DATA\\GB_ASOS_DATA\\GB_merged_ASOS_1980.csv',
 'F:\\JuPyterNotebook\\irp_ww721_bakcup\\data\\processed_data\\ASOS_DATA\\GB_ASOS_DATA\\GB_merged_ASOS_1981.csv',
 'F:\\JuPyterNotebook\\irp_ww721_bakcup\\data\\processed_data\\ASOS_DATA\\GB_ASOS_DATA\\GB_merged_ASOS_1982.csv',
 'F:\\JuPyterNotebook\\irp_ww721_bakcup\\data\\processed_data\\ASOS_DATA\\GB_ASOS_DATA\\GB_merged_ASOS_1983.csv',
 'F:\\JuPyterNotebook\\irp_ww721_bakcup\\data\\processed_data\\ASOS_DATA\\GB_ASOS_DATA\\GB_merged_ASOS_1984.csv',
 'F:\\JuPyterNotebook\\irp_ww721_bakcup\\data\\processed_data\\ASOS_DATA\\GB_ASOS_DATA\\GB_merged_ASOS_1985.csv',
 'F:\\JuPyterNotebook\\irp_ww721_bakcup\\data\\processed_data\\ASOS_DATA\\GB_ASOS_DATA\\GB_merged_ASOS_1986.csv',
 'F:\\JuPyterNotebook\\irp_ww721_bakcup\\data\\processed_data\\ASOS_DATA\\GB_ASOS_DATA\\

### csv_to_nc

In [ ]:
def csv_to_nc4(merged_csv_path,year, country, data_folder, data_category, output_folder):
    """Convert the merged CSV file to netCDF4 format by year."""
    df = pd.read_csv(merged_csv_path)
    ds_in = xr.Dataset.from_dataframe(df.set_index(['latitude', 'longitude', 'time']))
    ds_in = ds_in.sel(latitude=slice(50, 58), longitude=slice(-6, 2))
    ddeg_out_lat = 0.25
    ddeg_out_lon = 0.125
    regridded_ds = regrid(ds_in, ddeg_out_lat, ddeg_out_lon, method="bilinear", reuse_weights=False)

    output_directory = folder_utils.find_folder(country,data_folder,data_category,output_folder)
    output_filename = f"{country}_ASOS_regird_{year}.nc"
    output_path = os.path.join(output_directory, output_filename)
    regridded_ds.to_netcdf(output_path)
    print(f"{output_filename} done!")

In [146]:
parse_dates=["time"]
dtype_optimization = {
                't2m': 'float32',
                'latitude': 'float64',
                'longitude': 'float64',
            }
df = pd.read_csv(csv_paths[25],dtype=dtype_optimization, parse_dates=parse_dates)
df

latitude  longitude                time         t2m
0        57.2049    -2.2053 2004-01-01 00:00:00  276.000000
1        57.2049    -2.2053 2004-01-01 01:00:00  276.000000
2        57.2049    -2.2053 2004-01-01 02:00:00  276.500000
3        57.2049    -2.2053 2004-01-01 03:00:00  276.799988
4        57.2049    -2.2053 2004-01-01 04:00:00  277.299988
...          ...        ...                 ...         ...
550074   51.0063    -2.6428 2004-12-31 19:00:00  281.500000
550075   51.0063    -2.6428 2004-12-31 20:00:00  280.899994
550076   51.0063    -2.6428 2004-12-31 21:00:00  281.500000
550077   51.0063    -2.6428 2004-12-31 22:00:00  281.000000
550078   51.0063    -2.6428 2004-12-31 23:00:00  281.500000

[550079 rows x 4 columns]

In [218]:
import pandas as pd

# Assuming df is your DataFrame, and df['time'] is the time column
df['time'] = pd.to_datetime(df['time'])  # Ensure the data type of the time column is datetime

# Check if the time is a whole hour and not NULL
is_whole_hour = (df['time'].dt.minute == 0) & (df['time'].dt.second == 0)
not_null = df['time'].notnull()

# Check if latitude and longitude are within the specified range
latitude_condition = (df['latitude'] >= 50) & (df['latitude'] <= 58)
longitude_condition = (df['longitude'] >= -6) & (df['longitude'] <= 2)

# Combine all conditions
combined_condition = is_whole_hour & not_null & latitude_condition & longitude_condition

# Filter the DataFrame based on the conditions
filtered_df = df[combined_condition]

print(filtered_df)


        latitude  longitude                time         t2m
0        57.2049    -2.2053 2004-01-01 00:00:00  276.000000
1        57.2049    -2.2053 2004-01-01 01:00:00  276.000000
2        57.2049    -2.2053 2004-01-01 02:00:00  276.500000
3        57.2049    -2.2053 2004-01-01 03:00:00  276.799988
4        57.2049    -2.2053 2004-01-01 04:00:00  277.299988
...          ...        ...                 ...         ...
550074   51.0063    -2.6428 2004-12-31 19:00:00  281.500000
550075   51.0063    -2.6428 2004-12-31 20:00:00  280.899994
550076   51.0063    -2.6428 2004-12-31 21:00:00  281.500000
550077   51.0063    -2.6428 2004-12-31 22:00:00  281.000000
550078   51.0063    -2.6428 2004-12-31 23:00:00  281.500000

[540980 rows x 4 columns]


In [153]:
print(multi_indexed_df.head())

latitude  longitude  time               
57.2049   -2.2053    2004-01-01 00:00:00    276.000000
                     2004-01-01 01:00:00    276.000000
                     2004-01-01 02:00:00    276.500000
                     2004-01-01 03:00:00    276.799988
                     2004-01-01 04:00:00    277.299988
Name: t2m, dtype: float32


In [143]:
ds_in = ds_in.sel(latitude=slice(50, 58), longitude=slice(-6, 2))
ds_in

<xarray.Dataset>
Dimensions:    (latitude: 81, longitude: 81, time: 17455)
Coordinates:
  * latitude   (latitude) float64 50.08 50.42 50.44 50.74 ... 57.65 57.71 57.82
  * longitude  (longitude) float64 -5.873 -5.686 -5.257 ... 1.3 1.346 1.357
  * time       (time) datetime64[ns] 2004-01-01 ... 2004-12-31T23:00:00
Data variables:
    t2m        (latitude, longitude, time) float32 nan nan nan ... nan nan nan

In [193]:
ddeg_out_lat = 0.25
ddeg_out_lon = 0.125
regridded_ds = regrid(ds, ddeg_out_lat, ddeg_out_lon, method="bilinear", reuse_weights=False)

D:\anaconda3\envs\da\Lib\site-packages\xesmf\smm.py:130: UserWarning: Input array is not C_CONTIGUOUS. Will affect performance.
  warnings.warn('Input array is not C_CONTIGUOUS. ' 'Will affect performance.')


In [194]:
regridded_ds

<xarray.Dataset>
Dimensions:  (time: 8784, lat: 32, lon: 64)
Coordinates:
  * time     (time) datetime64[ns] 2004-01-01 ... 2004-12-29T11:00:00
  * lat      (lat) float64 50.0 50.25 50.5 50.75 51.0 ... 57.0 57.25 57.5 57.75
  * lon      (lon) float64 -6.0 -5.875 -5.75 -5.625 ... 1.5 1.625 1.75 1.875
Data variables:
    t2m      (time, lat, lon) float32 0.0 0.0 0.0 0.0 0.0 ... 0.0 0.0 0.0 0.0
Attributes:
    regrid_method:  bilinear

In [197]:
regridded_ds.t2m.values[12][12]

array([ 0.,  0., nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
       nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
       nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
       nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
       nan, nan, nan, nan, nan, nan, nan,  0.,  0.,  0.,  0.,  0.],
      dtype=float32)

In [ ]:
for year,csv_path in tqdm(zip(year_str_list,csv_paths)):
    csv_to_nc4(csv_path,year,country,data_folder,data_save_category,output_folder)

### Test on the big merged data and regird (memory issue not a good idea)

In [29]:
merged_df

latitude  longitude                 time    t2m
0          57.2049    -2.2053                  NaN    NaN
1          49.7061    -2.2147                  NaN    NaN
2          53.2527    -4.5365                  NaN    NaN
3          52.9622    -0.5616                  NaN    NaN
4          54.6135    -5.8735  1979-02-08 12:00:00    NaN
...            ...        ...                  ...    ...
24608122   52.6483     0.5670  2022-12-31 20:00:00  285.2
24608123   52.6483     0.5670  2022-12-31 21:00:00  284.2
24608124   52.6483     0.5670  2022-12-31 22:00:00  284.2
24608125   52.6483     0.5670  2022-12-31 23:00:00  285.2
24608126   52.6483     0.5670  2023-01-01 00:00:00  284.2

[24332112 rows x 4 columns]

In [20]:
merged_df.head(100)

latitude  longitude                 time  t2m
0    57.2049    -2.2053                  NaN  NaN
1    49.7061    -2.2147                  NaN  NaN
2    53.2527    -4.5365                  NaN  NaN
3    52.9622    -0.5616                  NaN  NaN
4    54.6135    -5.8735  1979-02-08 12:00:00  NaN
..       ...        ...                  ...  ...
95   54.6135    -5.8735  1979-02-22 16:00:00  NaN
96   54.6135    -5.8735  1979-02-23 09:00:00  NaN
97   54.6135    -5.8735  1979-02-23 10:00:00  NaN
98   54.6135    -5.8735  1979-02-23 12:00:00  NaN
99   54.6135    -5.8735  1979-02-23 13:00:00  NaN

[100 rows x 4 columns]

In [40]:
def save_asos_merged_data(
    merged_df, country, data_folder, data_category, output_folder
):
    output_directory = folder_utils.create_folder(
        country, data_folder, data_category, output_folder
    )
    output_filename = f"{country}_ASOS_merged_data.csv"
    output_filepath = os.path.join(output_directory, output_filename)
    merged_df.to_csv(output_filepath, index=False, encoding="utf-8")
    print(f"{output_filename} done!")
    return output_filepath

In [41]:
merged_csv_path = save_asos_merged_data(merged_df,country,data_folder,data_save_category, output_folder)

Folder 'F:\JuPyterNotebook\irp_ww721_bakcup\data\processed_data\ASOS_DATA\GB_ASOS_DATA' created successfully.
GB_ASOS_merged_data.csv done!


In [88]:
def csv_to_nc4(merged_csv_path, country, data_folder, data_category, output_folder):
    """Convert the merged CSV file to netCDF4 format by year."""
    try:
        # Function to process each partition to xarray Dataset
        def process_partition_to_xarray(df_partition):
            data_vars = {
                't2m': df_partition['t2m'].values
            }
            coords = {
                'latitude': df_partition['latitude'].values,
                'longitude': df_partition['longitude'].values,
                'time': df_partition['time'].values
            }
            ds = xr.Dataset(data_vars, coords=coords)
            return ds

        # 1. Use Dask's lazy computation strategy.
        chunksize = 200_000
        dtype_optimization = {
            't2m': 'float32',
            'latitude': 'float64',
            'longitude': 'float64',
        }

        merged_dask_df_iter = dd.read_csv(
            merged_csv_path,
            blocksize=chunksize,
            dtype=dtype_optimization,
            parse_dates=['time'],
            date_format='%Y-%m-%d %H:%M:%S'
        )

        output_directory = folder_utils.find_folder(
            country, data_folder, data_category, output_folder
        )

        meta = xr.DataArray(np.array([[[0.]]]),
                            coords={'latitude': [0.], 'longitude': [0.], 'time': [pd.Timestamp('2000-01-01')]},
                            dims=['latitude', 'longitude', 'time'],
                            name='t2m')
        print("tt")
        # Convert Dask DataFrame partitions to xarray and compute the result
        ds_list = merged_dask_df_iter.map_partitions(process_partition_to_xarray,meta=meta).compute().tolist()
        print("tt")
        # Combine chunks into one large dataset
        combined_ds = xr.concat(ds_list, dim='index')
        print("tt")
        # Further processing
        combined_ds = combined_ds.sel(latitude=slice(58, 50), longitude=slice(-6, 2))
        ddeg_out_lat = 0.25
        ddeg_out_lon = 0.125
        # regridded_ds = regrid(combined_ds, ddeg_out_lat, ddeg_out_lon, method="bilinear", reuse_weights=False)
        years = combined_ds["time.year"].unique().values

        with tqdm(years) as t_years:
            for year in t_years:
                year_ds = combined_ds.sel(time=str(year))
                output_filename_nc = f"{country}_ASOS_bf_regrid_data_{year}.nc"
                output_filepath = os.path.join(output_directory, output_filename_nc)
                year_ds.to_netcdf(output_filepath)
                print(f"{output_filename_nc} saved !")

        # Memory cleanup
        del combined_ds
        gc.collect()

        return True

    except Exception as e:
        print(f"Error processing and saving data: {e}")
        return False


In [42]:
merged_csv_path

'F:\\JuPyterNotebook\\irp_ww721_bakcup\\data\\processed_data\\ASOS_DATA\\GB_ASOS_DATA\\GB_ASOS_merged_data.csv'

In [54]:
def custom_date_parser(x):
    if pd.isna(x):
        return pd.NaT  
    return pd.to_datetime(x, format='%Y-%m-%d %H:%M:%S')

In [89]:
csv_to_nc4(merged_csv_path, country, data_folder, data_save_category, output_folder)

tt
Error processing and saving data: ('process_partition_to_xarray-eb6f2da036ef6c217965176d5a373e73', 0, 0, 0)


False

In [71]:
# 1. Use Dask's lazy computation strategy.
chunksize = 200_000
dtype_optimization = {
    't2m': 'float32',  # as era5 setting
    'latitude': 'float64',  # Optimize to float32 if sufficient.
    'longitude': 'float64',  # Optimize to float32 if sufficient.
}

# 2. Adjust chunk size
merged_dask_df_iter = dd.read_csv(
    merged_csv_path,
    blocksize=chunksize,
    dtype=dtype_optimization,
    parse_dates=['time'],
    date_format='%Y-%m-%d %H:%M:%S'
)

In [72]:
merged_dask_df_iter

Dask DataFrame Structure:
                 latitude longitude            time      t2m
npartitions=5159                                            
                  float64   float64  datetime64[ns]  float32
                      ...       ...             ...      ...
...                   ...       ...             ...      ...
                      ...       ...             ...      ...
                      ...       ...             ...      ...
Dask Name: read-csv, 1 graph layer

In [74]:
print(type(merged_dask_df_iter))
print(merged_dask_df_iter.head())


<class 'dask.dataframe.core.DataFrame'>
   latitude  longitude                time  t2m
0   57.2049    -2.2053                 NaT  NaN
1   49.7061    -2.2147                 NaT  NaN
2   53.2527    -4.5365                 NaT  NaN
3   52.9622    -0.5616                 NaT  NaN
4   54.6135    -5.8735 1979-02-08 12:00:00  NaN


In [78]:
print(pd.Timestamp('2000-01-01'))

2000-01-01 00:00:00


### ERA5 EDA(MAY delete later)

In [221]:
ds5 = xr.open_dataset("F:\JuPyterNotebook\irp_ww721_bakcup\data\processed_data\ERA5_DATA\GB_ERA5_DATA\era5_pressure_level_1983_regrid_850.nc")

In [237]:
ds5

<xarray.Dataset>
Dimensions:  (time: 8760, lat: 32, lon: 64)
Coordinates:
  * time     (time) datetime64[ns] 1983-01-01 ... 1983-12-31T23:00:00
  * lon      (lon) float64 -6.0 -5.875 -5.75 -5.625 ... 1.5 1.625 1.75 1.875
  * lat      (lat) float64 50.0 50.25 50.5 50.75 51.0 ... 57.0 57.25 57.5 57.75
Data variables:
    t        (time, lat, lon) float32 276.2 0.0 276.1 0.0 ... 276.5 276.5 276.6
Attributes:
    regrid_method:  bilinear
    Conventions:    CF-1.6
    history:        2023-08-26 12:29:25 GMT by grib_to_netcdf-2.25.1: /opt/ec...

In [223]:
ds5.t.values

array([[[276.1634 ,   0.     , 276.06772, ...,   0.     , 275.94693,
           0.     ],
        [276.0013 , 275.9087 , 275.81595, ..., 275.83258, 275.81595,
         275.8248 ],
        [275.97803, 275.82672, 275.67538, ..., 275.94586, 275.93317,
         275.9439 ],
        ...,
        [276.07584, 275.91553, 275.7552 , ..., 275.4525 , 275.32758,
         275.20255],
        [276.33148, 276.2689 , 276.20648, ..., 275.5982 , 275.46246,
         275.31094],
        [276.54053, 276.61072, 276.68106, ..., 275.64697, 275.5013 ,
         275.34116]],

       [[276.68353,   0.     , 276.31842, ...,   0.     , 275.92575,
           0.     ],
        [276.8163 , 276.62488, 276.43353, ..., 275.80768, 275.7792 ,
         275.78506],
        [276.9706 , 276.7977 , 276.6249 , ..., 275.90826, 275.8848 ,
         275.89554],
        ...,
        [275.66797, 275.4023 , 275.13654, ..., 275.87485, 275.80075,
         275.71277],
        [275.68176, 275.50977, 275.33783, ..., 276.03696, 275.9745 ,
   

In [230]:
filtered_df = filtered_df.sort_values(by=['latitude', 'longitude', 'time'])
ds7 = filtered_df.set_index(['latitude', 'longitude', 'time']).to_xarray()

In [231]:
ds7

<xarray.Dataset>
Dimensions:    (latitude: 81, longitude: 81, time: 8784)
Coordinates:
  * latitude   (latitude) float64 50.08 50.42 50.44 50.74 ... 57.65 57.71 57.82
  * longitude  (longitude) float64 -5.873 -5.686 -5.257 ... 1.3 1.346 1.357
  * time       (time) datetime64[ns] 2004-01-01 ... 2004-12-31T23:00:00
Data variables:
    t2m        (latitude, longitude, time) float32 nan nan nan ... nan nan nan

In [236]:
ds7.t2m.values[5][0]

array([nan, nan, nan, ..., nan, nan, nan], dtype=float32)